In [ ]:
import json
import os
import random
import argparse
from dataclasses import dataclass, field
from typing import Dict, List, Tuple, Optional
import numpy as np

In [ ]:
FRUITS = {
    "2021": ["apple", "avocado", "grape", "lemon"]
}

FRUIT_STATES = {
    "2021": {
        "agnostic": {
            "national demand": "Overall demand trends across the US consumer markets.",
            "input costs": "Costs of fertilizer, labor, and transportation.",
            "weather": "Major climate outcomes (normal, drought, heavy rain, early frost).",
        },
        "specific": {
            "price shock": lambda fruit: f"Large unexpected change in the price of {fruit} due to supply/demand shocks.",
            "pest outbreak": lambda fruit: f"Pest/disease incidence affecting {fruit} yields in the season.",
        },
    }
}

In [ ]:
class MockLLM:
    belief_phrases = ["very likely", "likely", "somewhat likely", "somewhat unlikely", "unlikely", "very unlikely"]

    @staticmethod
    def generate(prompt: str, system: Optional[str] = None, temperature: float = 0.0) -> str:

        if "produce a belief distribution" in prompt.lower() or "belief distribution" in prompt.lower():
            random.seed(len(prompt))
            state_lines = [line.strip().lstrip("- ").split(":")[0] for line in prompt.splitlines() if line.strip().startswith("- ")]
            result = {}
            for s in state_lines:
                options = [f"{s}_high", f"{s}_medium", f"{s}_low"]
                choices = random.sample(MockLLM.belief_phrases, 3)
                result[s] = {options[i]: choices[i] for i in range(3)}
            return json.dumps(result)
        elif "state-action pair" in prompt.lower() or "state-action pairs" in prompt.lower():
            lines = [l.strip() for l in prompt.splitlines() if l.strip().startswith("Action") or l.strip().startswith("- State-Action Pair")]
            scores = []
            idx = 0
            for l in lines:
                if "State-Action Pair" in l:
                    score = 0
                    if "avocado" in l:
                        score += 5
                    if "apple" in l:
                        score += 2
                    if "drought" in l:
                        score -= 1
                    scores.append((idx + 1, score))
                    idx += 1

            scores_sorted = sorted(scores, key=lambda x: -x[1])

            rank = [s[0] for s in scores_sorted]
            response = {"decision": f"State-Action Pair {rank[0]}", "rank": rank, "explanation": "Mocked ranking based on fruit preference heuristics."}
            return json.dumps(response)
        else:

            actions = [l.strip() for l in prompt.splitlines() if l.strip().startswith("Action")]

            chosen = None
            for a in actions:
                if "avocado" in a:
                    chosen = a
                    break
            if chosen is None and actions:
                chosen = random.choice(actions)
            response = {"decision": chosen or "Action 1", "explanation": "Mock decision: prefer avocado if available."}
            return json.dumps(response)


In [ ]:
def main():
    choices = FRUITS["2021"]
    budget = 10
    print(f"Available Crops: {', '.join(choices)}")
    print(f"Budget: {budget} acres\n")
    agent = DeLLMaAgent(
        choices=choices,
        year="2021",
        action_config=ActionConfig(budget=budget),
        state_config=StateConfig(states=FRUIT_STATES["2021"]["agnostic"]),
        preference_config=PreferenceConfig(),
        llm=MockLLM,
    )
    print("Generating belief distribution about external factors...")
    _, belief_raw = agent.generate_belief_distribution()
    print("Belief states prepared.\n")
    actions, _ = agent.prepare_actions()
    print("Possible actions:")
    for a in actions:
        print(f" - {a}")
    print()
    print("Evaluating state-action pairs using preference elicitation...")
    _, _, pref_response = agent.run_preference_elicitation()
    print(f"Top preferred pair (mocked LLM output): {pref_response['decision']}\n")
    print("Computing expected utility for each crop (sampling-based)...")
    best_action, utilities = agent.compute_best_action(samples_per_action=100)
    for a, u in utilities.items():
        print(f" - {a}: Expected Revenue = ${u:,.2f}")
    print("\nRecommended Action:")
    print(f"{best_action}")
    print(f"Estimated Profit: ${utilities[best_action]:,.2f}")

if __name__ == "__main__":
    main()


Available Crops: apple, avocado, grape, lemon
Budget: 10 acres

Generating belief distribution about external factors...
Belief states prepared.

Possible actions:
 - Action 1. apple: 10 acres
 - Action 2. avocado: 10 acres
 - Action 3. grape: 10 acres
 - Action 4. lemon: 10 acres

Evaluating state-action pairs using preference elicitation...
Top preferred pair (mocked LLM output): State-Action Pair 1

Computing expected utility for each crop (sampling-based)...
 - Action 1. apple: 10 acres: Expected Revenue = $199.92
 - Action 2. avocado: 10 acres: Expected Revenue = $327.60
 - Action 3. grape: 10 acres: Expected Revenue = $139.08
 - Action 4. lemon: 10 acres: Expected Revenue = $106.90

Recommended Action:
Action 2. avocado: 10 acres
Estimated Profit: $327.60
